In [1]:
import torch

# Confirm that the GPU is detected

assert torch.cuda.is_available()

# Get the GPU device name.

device_name = torch.cuda.get_device_name()
n_gpu = torch.cuda.device_count()
print(f"Found device: {device_name}, n_gpu: {n_gpu}")
device = torch.device("cuda")

# device = torch.device("mps")

Found device: NVIDIA GeForce RTX 3070 Laptop GPU, n_gpu: 1


In [2]:
!pip install torch
!pip install transformers
!pip install -U -q PyDrive
!pip install datasets
!pip install seqeval
!pip install ray[tune]

In [3]:
import os
import itertools
import pandas as pd
import numpy as np
from datasets import Dataset
from datasets import load_metric
from transformers import AutoTokenizer
from transformers import AutoModelForTokenClassification, TrainingArguments, Trainer
from transformers import DataCollatorForTokenClassification
import torch
from transformers import AutoTokenizer, AutoModelForSequenceClassification

tokenizer = AutoTokenizer.from_pretrained("nlpaueb/legal-bert-base-uncased")
model = AutoModelForSequenceClassification.from_pretrained("nlpaueb/legal-bert-base-uncased", num_labels=15) # num_labels = 14 + 1


Some weights of the model checkpoint at nlpaueb/legal-bert-base-uncased were not used when initializing BertForSequenceClassification: ['cls.predictions.transform.dense.weight', 'cls.seq_relationship.weight', 'cls.seq_relationship.bias', 'cls.predictions.decoder.bias', 'cls.predictions.transform.LayerNorm.weight', 'cls.predictions.bias', 'cls.predictions.transform.LayerNorm.bias', 'cls.predictions.transform.dense.bias', 'cls.predictions.decoder.weight']
- This IS expected if you are initializing BertForSequenceClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing BertForSequenceClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of BertForSequenceClassification wer

In [4]:
import pandas as pd

# from google.colab import drive
# drive.mount('/content/drive')
# %cd /content/drive/My Drive/Colab Notebooks/

import json

# from datasets import load_dataset, concatenate_datasets, Features, Value, ClassLabel, Sequence
# dataset = load_dataset('json', data_files='NER_JUDGEMENT_WikiAnn_Format.json')

import pandas as pd
train_df_judgement = pd.read_json('NER_TRAIN_JUDGEMENT_PREPROCESSED.json')
train_df_preamble = pd.read_json('NER_TRAIN_PREAMBLE_PREPROCESSED.json')

test_df_judgement = pd.read_json('NER_DEV_JUDGEMENT_PREPROCESSED.json')
test_df_preamble = pd.read_json('NER_DEV_PREAMBLE_PREPROCESSED.json')


In [5]:
print(len(train_df_judgement), len(train_df_preamble))
print(len(test_df_judgement), len(test_df_preamble))
total_data = len(train_df_judgement) + len(train_df_preamble) + len(test_df_judgement) + len(test_df_preamble)

8494 553
839 28


In [6]:
df = pd.concat([train_df_judgement, train_df_preamble])
df.reset_index(inplace=True, drop=True)
# print(df)
print(total_data)
split=int(total_data*0.7)
print(split)
train_df = df[:split]
val_df = df[split:]

test_df = pd.concat([test_df_judgement, test_df_preamble])

9914
6939


In [7]:
len(train_df)

6939

In [8]:
len(val_df)

2108

In [9]:
train_dataset = Dataset.from_pandas(train_df)
val_dataset = Dataset.from_pandas(val_df)
test_dataset = Dataset.from_pandas(test_df)

In [10]:
labels_list = ["COURT", "PETITIONER", "RESPONDENT", "JUDGE", "LAWYER", "DATE", "ORG", "GPE", "STATUTE", "PROVISION", "PRECEDENT", "CASE_NUMBER", "WITNESS", "OTHER_PERSON", "OTHERS"]
label_encoding_dict = {0: 0, 1: 1, 2: 2, 3: 3, 4: 4, 5: 5, 6: 6, 7: 7, 8: 8, 9: 9, 10: 10, 11: 11, 12: 12, 13: 13, 14: 14}
label_list_encoding_dict = {0: "OTHERS", 1: "PETITIONER", 2: "COURT", 3: "RESPONDENT", 4: "JUDGE", 5: "OTHER_PERSON", 6: "LAWYER", 7: "DATE", 8: "ORG", 9: "GPE", 10: "STATUTE", 11: "PROVISION", 12: "PRECEDENT", 13: "CASE_NUMBER", 14: "WITNESS"}

In [11]:
batch_size = 10

def tokenize_all_labels(rows):
    label_all = True
    tokenized_inputs = tokenizer(list(rows["tokens"]), truncation = True, is_split_into_words = True)
    labels = []
    for index, label in enumerate(rows["ner_tags"]):
        # print(i, label)
        previous_word_idx = None
        word_ids = tokenized_inputs.word_ids(batch_index = index)
        
        label_ids = []
        for word_idx in word_ids:
            if word_idx is None: label_ids.append(-100)
            elif label[word_idx] == '0': label_ids.append(0)
            elif word_idx != previous_word_idx: label_ids.append(label_encoding_dict[label[word_idx]])
            else: label_ids.append(label_encoding_dict[label[word_idx]] if label_all else -100)
            previous_word_idx = word_idx
        labels.append(label_ids)
        
    tokenized_inputs["labels"] = labels
    return tokenized_inputs


train_dataset_tokenized = train_dataset.map(tokenize_all_labels, batched=True)
val_dataset_tokenized = val_dataset.map(tokenize_all_labels, batched=True)

Map:   0%|          | 0/6939 [00:00<?, ? examples/s]

Map:   0%|          | 0/2108 [00:00<?, ? examples/s]

In [12]:
import os
# os.environ['TUNE_MAX_PENDING_TRIALS_PG'] = "1"
os.environ["TUNE_DISABLE_AUTO_CALLBACK_LOGGERS"] = "1"

In [13]:
from ray import tune
def ray_hp_space(trial):
    return {
        "learning_rate": tune.loguniform(1e-6, 1e-4),
        "per_device_train_batch_size": tune.choice([5, 8, 10]),
        "num_train_epochs": tune.choice([5, 10, 15])
    }

In [14]:
import warnings
warnings.filterwarnings('ignore')

metric = load_metric("seqeval")
tokenizer = AutoTokenizer.from_pretrained("nlpaueb/legal-bert-base-uncased")

def model_init():
    return AutoModelForTokenClassification.from_pretrained("nlpaueb/legal-bert-base-uncased", num_labels=len(labels_list))

training_arguments = TrainingArguments(
    "eval_indian_legal_ner",
    evaluation_strategy = "epoch",
    learning_rate=1e-6,
    per_device_train_batch_size=batch_size,
    per_device_eval_batch_size=batch_size,
    num_train_epochs=3,
    weight_decay=1e-5,
)

data_collator = DataCollatorForTokenClassification(tokenizer)

def evaluate_metrics(p):
    predictions, labels = p
    predictions = np.argmax(predictions, axis=2)

    actual_predictions = [[labels_list[p] for (p, l) in zip(prediction, label) if l != -100] for prediction, label in zip(predictions, labels)]
    actual_labels = [[labels_list[l] for (p, l) in zip(prediction, label) if l != -100] for prediction, label in zip(predictions, labels)]
    results = metric.compute(predictions=actual_predictions, references=actual_labels)
    return {"precision": results["overall_precision"], "recall": results["overall_recall"], "f1": results["overall_f1"], "accuracy": results["overall_accuracy"]}

def compute(metrics):
    return metrics["eval_accuracy"]
    
trainer = Trainer(
    model=None,
    args = training_arguments,
    train_dataset = train_dataset_tokenized,
    eval_dataset = val_dataset_tokenized,
    data_collator = data_collator,
    tokenizer = tokenizer,
    model_init = model_init,
    compute_metrics = evaluate_metrics
)
best_trial = trainer.hyperparameter_search(
    direction="maximize",
    backend="ray",
    hp_space=ray_hp_space,
    n_trials=6,
    compute_objective=compute
)

Some weights of the model checkpoint at nlpaueb/legal-bert-base-uncased were not used when initializing BertForTokenClassification: ['cls.predictions.transform.dense.weight', 'cls.seq_relationship.weight', 'cls.seq_relationship.bias', 'cls.predictions.decoder.bias', 'cls.predictions.transform.LayerNorm.weight', 'cls.predictions.bias', 'cls.predictions.transform.LayerNorm.bias', 'cls.predictions.transform.dense.bias', 'cls.predictions.decoder.weight']
- This IS expected if you are initializing BertForTokenClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing BertForTokenClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of BertForTokenClassification were not initia

== Status ==
Current time: 2023-05-03 20:01:31 (running for 00:00:00.05)
Using FIFO scheduling algorithm.
Logical resource usage: 1.0/16 CPUs, 1.0/1 GPUs
Result logdir: C:\Users\kavya\ray_results\_objective_2023-05-03_20-01-31
Number of trials: 6/6 (5 PENDING, 1 RUNNING)
+------------------------+----------+-----------------+-----------------+--------------------+------------------------+
| Trial name             | status   | loc             |   learning_rate |   num_train_epochs |   per_device_train_bat |
|                        |          |                 |                 |                    |                ch_size |
|------------------------+----------+-----------------+-----------------+--------------------+------------------------|
| _objective_d31e6_00000 | RUNNING  | 127.0.0.1:17704 |     5.61152e-06 |                 15 |                      5 |
| _objective_d31e6_00001 | PENDING  |                 |     2.91064e-05 |                  5 |                      5 |
| _objec

(_objective pid=17704) Some weights of the model checkpoint at nlpaueb/legal-bert-base-uncased were not used when initializing BertForTokenClassification: ['cls.seq_relationship.bias', 'cls.predictions.transform.dense.weight', 'cls.predictions.bias', 'cls.predictions.transform.LayerNorm.bias', 'cls.predictions.decoder.weight', 'cls.predictions.transform.LayerNorm.weight', 'cls.predictions.decoder.bias', 'cls.predictions.transform.dense.bias', 'cls.seq_relationship.weight']
(_objective pid=17704) - This IS expected if you are initializing BertForTokenClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
(_objective pid=17704) - This IS NOT expected if you are initializing BertForTokenClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassificati

== Status ==
Current time: 2023-05-03 20:01:42 (running for 00:00:11.36)
Using FIFO scheduling algorithm.
Logical resource usage: 1.0/16 CPUs, 1.0/1 GPUs
Result logdir: C:\Users\kavya\ray_results\_objective_2023-05-03_20-01-31
Number of trials: 6/6 (5 PENDING, 1 RUNNING)
+------------------------+----------+-----------------+-----------------+--------------------+------------------------+
| Trial name             | status   | loc             |   learning_rate |   num_train_epochs |   per_device_train_bat |
|                        |          |                 |                 |                    |                ch_size |
|------------------------+----------+-----------------+-----------------+--------------------+------------------------|
| _objective_d31e6_00000 | RUNNING  | 127.0.0.1:17704 |     5.61152e-06 |                 15 |                      5 |
| _objective_d31e6_00001 | PENDING  |                 |     2.91064e-05 |                  5 |                      5 |
| _objec

  1%|          | 107/20820 [00:07<24:28, 14.11it/s]


...

== Status ==
Current time: 2023-05-03 21:58:04 (running for 01:56:33.10)
Using FIFO scheduling algorithm.
Logical resource usage: 1.0/16 CPUs, 1.0/1 GPUs
Result logdir: C:\Users\kavya\ray_results\_objective_2023-05-03_20-01-31
Number of trials: 6/6 (1 RUNNING, 5 TERMINATED)
+------------------------+------------+-----------------+-----------------+--------------------+------------------------+-------------+
| Trial name             | status     | loc             |   learning_rate |   num_train_epochs |   per_device_train_bat |   objective |
|                        |            |                 |                 |                    |                ch_size |             |
|------------------------+------------+-----------------+-----------------+--------------------+------------------------+-------------|
| _objective_d31e6_00005 | RUNNING    | 127.0.0.1:29540 |     2.65875e-06 |                  5 |                      5 |    0.761589 |
| _objective_d31e6_00000 | TERMINATED | 127.0

(_objective pid=29540) 
 54%|█████▍    | 114/211 [00:03<00:02, 33.91it/s]
(_objective pid=29540) 
 56%|█████▌    | 118/211 [00:03<00:02, 35.16it/s]
(_objective pid=29540) 
 58%|█████▊    | 122/211 [00:03<00:02, 33.24it/s]
(_objective pid=29540) 
 60%|█████▉    | 126/211 [00:03<00:02, 32.62it/s]
(_objective pid=29540) 
 62%|██████▏   | 130/211 [00:03<00:02, 33.54it/s]
(_objective pid=29540) 
 64%|██████▎   | 134/211 [00:03<00:02, 33.34it/s]
(_objective pid=29540) 
 65%|██████▌   | 138/211 [00:04<00:02, 32.88it/s]
(_objective pid=29540) 
 67%|██████▋   | 142/211 [00:04<00:02, 34.14it/s]
(_objective pid=29540) 
 69%|██████▉   | 146/211 [00:04<00:01, 34.67it/s]
(_objective pid=29540) 
 71%|███████   | 150/211 [00:04<00:01, 33.93it/s]
(_objective pid=29540) 
 73%|███████▎  | 154/211 [00:04<00:01, 34.76it/s]
(_objective pid=29540) 
 75%|███████▍  | 158/211 [00:04<00:02, 17.68it/s]
(_objective pid=29540) 
 76%|███████▋  | 161/211 [00:05<00:03, 15.50it/s]
(_objective pid=29540) 
 78%|███████▊ 

== Status ==
Current time: 2023-05-03 21:58:09 (running for 01:56:38.17)
Using FIFO scheduling algorithm.
Logical resource usage: 1.0/16 CPUs, 1.0/1 GPUs
Result logdir: C:\Users\kavya\ray_results\_objective_2023-05-03_20-01-31
Number of trials: 6/6 (1 RUNNING, 5 TERMINATED)
+------------------------+------------+-----------------+-----------------+--------------------+------------------------+-------------+
| Trial name             | status     | loc             |   learning_rate |   num_train_epochs |   per_device_train_bat |   objective |
|                        |            |                 |                 |                    |                ch_size |             |
|------------------------+------------+-----------------+-----------------+--------------------+------------------------+-------------|
| _objective_d31e6_00005 | RUNNING    | 127.0.0.1:29540 |     2.65875e-06 |                  5 |                      5 |    0.761589 |
| _objective_d31e6_00000 | TERMINATED | 127.0

(_objective pid=29540) 
 93%|█████████▎| 196/211 [00:08<00:01, 11.63it/s]
(_objective pid=29540) 
 94%|█████████▍| 198/211 [00:08<00:01, 12.35it/s]
(_objective pid=29540) 
 95%|█████████▍| 200/211 [00:08<00:01, 10.76it/s]
(_objective pid=29540) 
 96%|█████████▌| 202/211 [00:09<00:00, 10.63it/s]
(_objective pid=29540) 
 97%|█████████▋| 204/211 [00:09<00:00,  9.17it/s]
(_objective pid=29540) 
 98%|█████████▊| 206/211 [00:09<00:00,  9.47it/s]
(_objective pid=29540) 
 99%|█████████▉| 209/211 [00:09<00:00, 10.99it/s]
(_objective pid=29540) 
100%|██████████| 211/211 [00:09<00:00, 10.39it/s]
(_objective pid=29540) C:\Users\kavya\AppData\Local\Programs\Python\Python38\lib\site-packages\seqeval\metrics\sequence_labeling.py:171: UserWarning: COURT seems not to be NE tag.
(_objective pid=29540)   warnings.warn('{} seems not to be NE tag.'.format(chunk))
(_objective pid=29540) C:\Users\kavya\AppData\Local\Programs\Python\Python38\lib\site-packages\seqeval\metrics\sequence_labeling.py:171: UserWarn

== Status ==
Current time: 2023-05-03 21:58:13 (running for 01:56:42.73)
Using FIFO scheduling algorithm.
Logical resource usage: 0/16 CPUs, 0/1 GPUs
Result logdir: C:\Users\kavya\ray_results\_objective_2023-05-03_20-01-31
Number of trials: 6/6 (6 TERMINATED)
+------------------------+------------+-----------------+-----------------+--------------------+------------------------+-------------+
| Trial name             | status     | loc             |   learning_rate |   num_train_epochs |   per_device_train_bat |   objective |
|                        |            |                 |                 |                    |                ch_size |             |
|------------------------+------------+-----------------+-----------------+--------------------+------------------------+-------------|
| _objective_d31e6_00000 | TERMINATED | 127.0.0.1:17704 |     5.61152e-06 |                 15 |                      5 |    0.814016 |
| _objective_d31e6_00001 | TERMINATED | 127.0.0.1:28204 |   

In [15]:
best_trial

BestRun(run_id='d31e6_00001', objective=0.8183060335547128, hyperparameters={'learning_rate': 2.910635913133073e-05, 'per_device_train_batch_size': 5, 'num_train_epochs': 5}, run_summary=<ray.tune.analysis.experiment_analysis.ExperimentAnalysis object at 0x000001F62ED0BB20>)

In [16]:
import warnings
warnings.filterwarnings('ignore')

batch_size = 5
epoch = 5
learning_rate = 2.910635913133073e-05

tokenizer = AutoTokenizer.from_pretrained("nlpaueb/legal-bert-base-uncased")
model = AutoModelForTokenClassification.from_pretrained("nlpaueb/legal-bert-base-uncased", num_labels=len(labels_list))
metric = load_metric("seqeval")

training_arguments = TrainingArguments(
    "eval_indian_legal_ner",
    evaluation_strategy = "epoch",
    learning_rate=learning_rate,
    per_device_train_batch_size=batch_size,
    per_device_eval_batch_size=batch_size,
    num_train_epochs=epoch,
    weight_decay=1e-5,
)

data_collator = DataCollatorForTokenClassification(tokenizer)

def evaluate_metrics(p):
    predictions, labels = p
    predictions = np.argmax(predictions, axis=2)

    actual_predictions = [[labels_list[p] for (p, l) in zip(prediction, label) if l != -100] for prediction, label in zip(predictions, labels)]
    actual_labels = [[labels_list[l] for (p, l) in zip(prediction, label) if l != -100] for prediction, label in zip(predictions, labels)]
    results = metric.compute(predictions=actual_predictions, references=actual_labels)
    return {"precision": results["overall_precision"], "recall": results["overall_recall"], "f1": results["overall_f1"], "accuracy": results["overall_accuracy"]}
    
trainer = Trainer(
    model,
    training_arguments,
    train_dataset = train_dataset_tokenized,
    eval_dataset = val_dataset_tokenized,
    data_collator = data_collator,
    tokenizer=tokenizer,
    compute_metrics=evaluate_metrics
)
trainer.train()
trainer.evaluate()
trainer.save_model('indian_legal_ner.model')

Some weights of the model checkpoint at nlpaueb/legal-bert-base-uncased were not used when initializing BertForTokenClassification: ['cls.predictions.transform.dense.weight', 'cls.seq_relationship.weight', 'cls.seq_relationship.bias', 'cls.predictions.decoder.bias', 'cls.predictions.transform.LayerNorm.weight', 'cls.predictions.bias', 'cls.predictions.transform.LayerNorm.bias', 'cls.predictions.transform.dense.bias', 'cls.predictions.decoder.weight']
- This IS expected if you are initializing BertForTokenClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing BertForTokenClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of BertForTokenClassification were not initia

In [17]:
test_dataset_tokenized = test_dataset.map(tokenize_all_labels, batched=True)

Map:   0%|          | 0/867 [00:00<?, ? examples/s]

In [18]:
test_results = trainer.evaluate(test_dataset_tokenized)

In [19]:
test_results

{'eval_loss': 0.25835496187210083,
 'eval_precision': 0.7827083333333333,
 'eval_recall': 0.8461711711711711,
 'eval_f1': 0.8132034632034632,
 'eval_accuracy': 0.9221969509311595,
 'eval_runtime': 4.5592,
 'eval_samples_per_second': 190.164,
 'eval_steps_per_second': 38.164,
 'epoch': 5.0}